In [1]:
!pip install sagemaker --upgrade
!pip install boto3 --upgrade

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.7/1.7 MB 93.7 MB/s eta 0:00:00
  Attempting uninstall: sagemaker
    Found existing installation: sagemaker 2.246.0
    Uninstalling sagemaker-2.246.0:
      Successfully uninstalled sagemaker-2.246.0
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.7/13.7 MB 171.8 MB/s eta 0:00:00
  Attempting uninstall: botocore
    Found existing installation: botocore 1.38.35
    Uninstalling botocore-1.38.35:━━━━━━━━━━━━━━ 0/2 [botocore]
      Successfully uninstalled botocore-1.38.35m 0/2 [botocore]
  Attempting uninstall: boto3━━━━━━━━━━━━━━━━━━━ 0/2 [botocore]
    Found existing installation: boto3 1.38.35m━━━━━━━━━━━━━━━━━━━ 1/2 [boto3]
    Uninstalling boto3-1.38.35:0m╺━━━━━━━━━━━━━━━━━━━ 1/2 [boto3]
      Successfully uninstalled boto3-1.38.35━━━━━━━━━━━━━━━━━━ 1/2 [boto3]
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2/2 [boto3]32m1/2 [boto3]
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. T

In [2]:
import sagemaker
import boto3
sess = sagemaker.Session()
# sagemaker session bucket -> used for uploading data, models and logs
# sagemaker will automatically create this bucket if it not exists
sagemaker_session_bucket=None
if sagemaker_session_bucket is None and sess is not None:
    # set to default bucket if a bucket name is not given
    sagemaker_session_bucket = sess.default_bucket()

try:
    role = sagemaker.get_execution_role()
except ValueError:
    iam = boto3.client('iam')
    role = iam.get_role(RoleName='sagemaker_execution_role')['Role']['Arn']

sess = sagemaker.Session(default_bucket=sagemaker_session_bucket)

print(f"sagemaker role arn: {role}")
print(f"sagemaker bucket: {sess.default_bucket()}")
print(f"sagemaker session region: {sess.boto_region_name}")

sagemaker.config INFO - Not applying SDK defaults from location: /etc/xdg/sagemaker/config.yaml
sagemaker.config INFO - Not applying SDK defaults from location: /home/ec2-user/.config/sagemaker/config.yaml
sagemaker role arn: arn:aws:iam::637423338589:role/service-role/AmazonSageMakerServiceCatalogProductsUseRole
sagemaker bucket: sagemaker-us-east-1-637423338589
sagemaker session region: us-east-1


In [3]:
from sagemaker.huggingface.model import HuggingFaceModel
from sagemaker.serverless import ServerlessInferenceConfig

# Hub Model configuration. <https://huggingface.co/models>
hub = {
    'HF_MODEL_ID':'distilbert-base-uncased-finetuned-sst-2-english',
    'HF_TASK':'text-classification'
}

# create Hugging Face Model Class
huggingface_model = HuggingFaceModel(
   env=hub,                      # configuration for loading model from Hub
   role=role,                    # iam role with permissions to create an Endpoint
   transformers_version="4.26",  # transformers version used
   pytorch_version="1.13",        # pytorch version used
   py_version='py39',            # python version used
)

print("huggingface_model", huggingface_model)

huggingface_model <sagemaker.huggingface.model.HuggingFaceModel object at 0x7f1945adc8b0>


In [4]:
# Specify MemorySizeInMB and MaxConcurrency in the serverless config object
serverless_config = ServerlessInferenceConfig(
    memory_size_in_mb=4096, max_concurrency=10,
)

# deploy the endpoint endpoint
predictor = huggingface_model.deploy(
    serverless_inference_config=serverless_config
)

---!

In [ ]:
data = {
  "inputs": "the mesmerizing performances of the leads keep the film grounded and keep the audience riveted .",
}

res = predictor.predict(data=data)
print(res)

In [ ]:
predictor.delete_model()
predictor.delete_endpoint()
